# Analysing memory usage

In [1]:
import numpy as np
np.float32(1.1678236876823)

1.1678237

In [2]:
from components.model import get_income_and_attitude_weights
import sys
from pympler.asizeof import asizeof


incomes, weights = get_income_and_attitude_weights(700, 0.6)

print(sys.getsizeof(incomes),sys.getsizeof(weights))
asizeof(incomes),asizeof(weights) 
# (5728, 41368) 13.03.24
# (2928, 24568) after np.float32


2912 8544


(2928, 24568)

In [3]:
from data.canada import uncertain_demand_from_income_and_province, get_end_use_agg_heating_share


demand = uncertain_demand_from_income_and_province(incomes, "Ontario")
agg_heat_share = get_end_use_agg_heating_share("Ontario", 2000)
print(sys.getsizeof(demand),sys.getsizeof(agg_heat_share))
asizeof(demand),asizeof(agg_heat_share)
# (5728, 48)

2912 32


(2928, 48)

In [4]:
from components.technologies import merge_heating_techs_with_share
import pandas as pd

heat_tech_shares = merge_heating_techs_with_share(2000, "Ontario")
print(sys.getsizeof(heat_tech_shares))
# heat_tech_shares[:] = np.float16(heat_tech_shares.values)

asizeof(heat_tech_shares.astype("float16"))

948


25720

In [5]:
from components.model import TechnologyAdoptionModel

model = TechnologyAdoptionModel(700, "Ontario")
print(sys.getsizeof(model))
asizeof(model) 
# holy smokes! 963243912 13.03.24
# 693435952 after some float32 conversions

/mnt/speicher/.wissmit/david/.conda/envs/cando/lib/python3.10/site-packages/mesa/time.py:79: FutureWarning: The AgentSet is experimental. It may be changed or removed in any and all future releases, including patch releases.
We would love to hear what you think about this new feature. If you have any thoughts, share them with us here: https://github.com/projectmesa/mesa/discussions/1919
  self._agents: AgentSet = AgentSet(agents, model)


48


693435952

In [15]:
fuel_demands = model.schedule.agents[0].potential_fuel_demands
asizeof(fuel_demands),asizeof(fuel_demands.astype("int32"))

(853328, 853328)

In [19]:
model.schedule.agents[0].heat_demand_ts.resample("1w").sum()

time
2013-01-06    7.279832e+06
2013-01-13    6.132305e+06
2013-01-20    8.301508e+06
2013-01-27    1.089727e+07
2013-02-03    8.458061e+06
2013-02-10    9.749790e+06
2013-02-17    9.521732e+06
2013-02-24    9.115593e+06
2013-03-03    8.722358e+06
2013-03-10    7.620398e+06
2013-03-17    7.996011e+06
2013-03-24    8.119524e+06
2013-03-31    6.229418e+06
2013-04-07    7.099062e+06
2013-04-14    6.142495e+06
2013-04-21    4.938880e+06
2013-04-28    4.884688e+06
2013-05-05    2.903424e+06
2013-05-12    3.189291e+06
2013-05-19    3.074093e+06
2013-05-26    2.776205e+06
2013-06-02    1.141528e+06
2013-06-09    2.140773e+06
2013-06-16    1.125251e+06
2013-06-23    7.982491e+05
2013-06-30    2.996081e+05
2013-07-07    1.614716e+05
2013-07-14    2.128179e+05
2013-07-21    8.065862e+04
2013-07-28    5.651176e+05
2013-08-04    6.120968e+05
2013-08-11    3.408527e+05
2013-08-18    7.529462e+05
2013-08-25    1.543476e+05
2013-09-01    1.691692e+04
2013-09-08    1.084976e+06
2013-09-15    1.258557e

In [1]:
from components.probability import beta_with_mode_at
from components.technologies import Technologies

dist_params = dict(zip(Technologies,[0.5]*len(Technologies)))

atts = model.draw_attitudes_from_distribution(beta_with_mode_at, dist_params)
print(sys.getsizeof(atts))
asizeof(atts)
# 74640

NameError: name 'model' is not defined

In [28]:
atts

Gas furnace  Oil furnace  Wood or wood pellets furnace  Electric furnace  \
0       0.141724    -0.189819                      0.150635          0.251221   
1      -0.101746    -0.276855                     -0.031067         -0.364990   
2       0.748535    -0.062042                     -0.106812         -0.093689   
3       0.105591     0.165405                     -0.243652         -0.144409   
4       0.189453    -0.296387                      0.036530          0.138916   
..           ...          ...                           ...               ...   
695     0.536621     0.348633                     -0.144409         -0.046539   
696    -0.201904    -0.082397                     -0.397461          0.187622   
697     0.194702     0.013420                      0.114807          0.117859   
698     0.192749     0.063232                     -0.322510          0.221680   
699    -0.116577     0.205078                     -0.317383         -0.058502   

     Heat pump  
0     0.119019  
1    -0.056580  
2    -0.132812  
3    -0.292969  
4    -0.074707  
..         ...  
695  -0.096741  
696  -0.264404  
697   0.294434  
698   0.058502  
699  -0.468018  

[700 rows x 5 columns]

# The parameter fit

In [20]:
import pandas as pd

from components.model import TechnologyAdoptionModel
from components.technologies import Technologies
from components.probability import beta_with_mode_at
from data.canada import nrcan_tech_shares_df

from batch import BatchResult

historic_tech_shares = nrcan_tech_shares_df.copy()
historic_tech_shares.index = historic_tech_shares.index.swaplevel()
tech_mode_map = dict(zip(Technologies, [0.5] * len(Technologies)))

province = "Ontario"
gut = 0.33
p_mode = 0.33

h_tech_shares = historic_tech_shares.loc[province, :] / 100
att_mode_table = h_tech_shares.copy()


In [21]:


batch_parameters = {
    "N": [50],
    "province": [province],  # , "Alberta", "Ontario"],
    "random_seed": range(20, 23),
    "start_year": 2000,
    "tech_att_mode_table": [att_mode_table.copy()],
    "n_segregation_steps": [60],
    "interact": [False],
    "global_util_thresh": [gut]
}
print("price weight mode:", p_mode)
batch_parameters["price_weight_mode"] = p_mode

full_years = range(2000,2021)
scale = 2

price weight mode: 0.33


In [22]:

att_mode_tables = []
adoption_share_dfs = []
adoption_detail_dfs = []
mode_shift = 0.2
best_abs_diff = 1e12
greatest_diff_sum = None

n_fit_iterations = 3

for i in range(n_fit_iterations):
    
    b_result = BatchResult.from_parameters(batch_parameters)
    model_shares = b_result.tech_shares_df.groupby(["province","year"]).mean().drop("RunId",axis=1)
    diff = (h_tech_shares - model_shares.loc[(province,full_years),:]).loc[province,:]
    
    tech_share_abs_diff = diff.abs().sum()
    current_abs_diff = tech_share_abs_diff.sum()
    print(i, current_abs_diff)
    
    # if current is not smallest diff
    if best_abs_diff <= current_abs_diff:
        print("Performance degradation. Scaling down mode_shift")
        scale /= 2
        att_update = diff * scale
    else:
        best_abs_diff = current_abs_diff
        best_modes = att_mode_table.copy()
        att_update = diff * scale
    # print("applying cumulative update of:", att_update.abs().sum())
    att_mode_table = att_mode_table + att_update
    
    # adjust modes to where distributions are sensible
    att_mode_table[att_mode_table<0.05] = 0.05
    att_mode_table[att_mode_table>0.95] = 0.95
    
    protocol_table = att_mode_table.copy()
    protocol_table["iteration"] = i
    att_mode_tables.append(protocol_table)
    
    model_shares["iteration"] = i
    adoption_share_dfs.append(model_shares)


    print(i, diff.abs().sum())
    batch_parameters["tech_att_mode_table"] = [att_mode_table]


results_dir=WindowsPath('c:/src/canadopt/abetam/results/feature_temporal_attitudes/2cb145f260ba6716f57c3e73865f33a2') does not exist. Running model.


100%|██████████| 3/3 [00:12<00:00,  4.08s/it]


0 3.7657760607672013
0 Electric furnace                1.131700
Gas furnace                     1.616274
Heat pump                       0.554670
Oil furnace                     0.284110
Wood or wood pellets furnace    0.179021
dtype: float64
results_dir=WindowsPath('c:/src/canadopt/abetam/results/feature_temporal_attitudes/2cb145f260ba6716f57c3e73865f33a2') does not exist. Running model.


100%|██████████| 3/3 [00:11<00:00,  3.95s/it]


1 3.752442727433868
1 Electric furnace                1.125034
Gas furnace                     1.609607
Heat pump                       0.554670
Oil furnace                     0.284110
Wood or wood pellets furnace    0.179021
dtype: float64
results_dir=WindowsPath('c:/src/canadopt/abetam/results/feature_temporal_attitudes/2cb145f260ba6716f57c3e73865f33a2') does not exist. Running model.


100%|██████████| 3/3 [00:12<00:00,  4.07s/it]

2 3.405776060767201
2 Electric furnace                0.951700
Gas furnace                     1.436274
Heat pump                       0.554670
Oil furnace                     0.284110
Wood or wood pellets furnace    0.179021
dtype: float64


In [24]:
import plotly.express as px
all_attitude_modes = pd.concat(att_mode_tables)
all_attitude_modes = all_attitude_modes.melt(id_vars=["iteration"], ignore_index=False).reset_index()
px.line(all_attitude_modes, x="year", y="value", color="variable", line_dash="iteration", template="plotly")

In [25]:
adoption_shares = pd.concat(adoption_share_dfs).loc[province,:].melt(id_vars=["iteration"], ignore_index=False).reset_index()
px.line(adoption_shares, x="year", y="value", color="variable", line_dash="iteration", template="plotly")

# Analysing parameter fit results

In [2]:
import pandas as pd
import plotly.express as px
from pathlib import Path
# results_dir = "results/fitting/2024.02.26-14.39"
results_dir = "results/fitting/2024.03.12-16.03"

def file_in_dir_like(dir, name_frag, suffix=".csv"):
    matches = list(Path(results_dir).glob(f"*{name_frag}*{suffix}"))
    if len(matches) != 1:
        raise ValueError(f"found {matches}, proceeding not defined")
    return matches[0]
att_mode_table = pd.read_csv(file_in_dir_like(results_dir,"all_attitude_modes"))


In [5]:
atts = att_mode_table.query("variable!='province'")
atts["value"] = atts["value"].astype(float)
fig = px.line(atts, x="year", y="value", color="variable", facet_col="p_mode", facet_row="gut", line_dash="iteration", template="plotly")
fig.update_traces(opacity=.2)


/tmp/ipykernel_1564942/1970221014.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [4]:
best_modes = pd.read_csv(file_in_dir_like(results_dir, "best_modes"))
best_modes[["best_abs_diff", "province", "gut", "p_mode",]].groupby(["province","gut","p_mode"]).mean().reset_index().pivot(index=["province","gut"], columns="p_mode", values="best_abs_diff")

p_mode             0.2       0.4       0.5       0.6
province gut                                        
Ontario  0.2  0.911347  0.915193  0.897683  0.783779
         0.3  0.736513  0.728357  1.272188  2.089650
         0.4  0.674388  2.085175  2.973177  3.341555

In [6]:
tech_shares = pd.read_csv(file_in_dir_like(results_dir, "historic_tech"))
tech_shares.head()

Unnamed: 0 province     year  iteration          variable     value  gut  \
0           0  Ontario  2000.00          0  Electric furnace  0.161429  0.2   
1           1  Ontario  2000.25          0  Electric furnace  0.160238  0.2   
2           2  Ontario  2000.50          0  Electric furnace  0.157857  0.2   
3           3  Ontario  2000.75          0  Electric furnace  0.156667  0.2   
4           4  Ontario  2001.00          0  Electric furnace  0.155476  0.2   

   p_mode  
0     0.2  
1     0.2  
2     0.2  
3     0.2  
4     0.2

In [20]:
from data.canada import nrcan_tech_shares_df

fig = px.line(tech_shares, x="year", y="value", color="variable", facet_col="p_mode", facet_row="gut", line_dash="iteration", template="plotly")

province="Ontario"
historic_tech_shares = nrcan_tech_shares_df.copy()
historic_tech_shares.index = historic_tech_shares.index.swaplevel()
h_tech_shares = historic_tech_shares.loc[province, :] / 100

h_tech_shares_long = h_tech_shares.melt(ignore_index=False)

hist_fig = px.line(h_tech_shares_long.reset_index(), x="year", y="value", color="variable", template="plotly")

for i,col in enumerate(tech_shares.p_mode.unique()):
    for j, row in enumerate(tech_shares.gut.unique()):
        for trace in hist_fig.data:
            fig.add_trace(trace, row=j+1, col=i+1)
        

In [21]:
fig